Importing IMF GDP Per capita data to use as target values\
Data include GDP per capita for every country for all years available.

In [1]:
import pandas as pd
import time
import numpy as np
from datetime import date

import random

from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import MinMaxScaler

from statsmodels.stats.outliers_influence import variance_inflation_factor
from statsmodels.tools.tools import add_constant

from sklearn.tree import DecisionTreeRegressor

from sklearn.model_selection import KFold

import altair as alt
from vega_datasets import data

from sklearn.inspection import permutation_importance

from sklearn.metrics import mean_squared_error
import math


In [2]:
# imf_target_values_import=pd.read_excel(open('/Users/stephenontko/Documents/University of Michigan/UMSI/UMSI MADS/UMSI MADS 2023/SIADS 699 Capstone/Data/IMF/imf-dm-export-20230215.xlsx','rb'),sheet_name='NGDPDPC')
imf_target_values_import=pd.read_csv('imf-dm-export-20230215.csv')


imf_target_values_import = imf_target_values_import.iloc[1:,:]
print(imf_target_values_import)

    GDP per capita, current prices\n (U.S. dollars per capita)      1980  \
1                                          Afghanistan           no data   
2                                              Albania           728.359   
3                                              Algeria          2268.607   
4                                              Andorra           no data   
5                                               Angola           745.119   
..                                                 ...               ...   
226                           Other advanced economies          6886.485   
227                                 Sub-Saharan Africa           no data   
228                                              World          2862.333   
229                                                NaN               NaN   
230                                         ©IMF, 2022               NaN   

         1981      1982      1983      1984      1985      1986       1987  \
1     no 

In [3]:
imf_target_values_import.index.name = 'Country'

file_model_df = imf_target_values_import.copy()

file_model_df.index.name = 'Country'

file_model_df['Country Name'] = file_model_df['GDP per capita, current prices\n (U.S. dollars per capita)']
file_model_df.index = file_model_df['Country Name']
file_model_df=file_model_df.drop(columns = ['Country Name','GDP per capita, current prices\n (U.S. dollars per capita)'])

file_model_df.set_axis([int(x) for x in file_model_df.columns],axis = 'columns', inplace=True)

file_model_df=file_model_df.replace('no data',0)
file_model_df=file_model_df.fillna(0)
file_model_df = file_model_df.loc[file_model_df.index.notna()]


country_exclusion_list = [
'Africa (Region)',
'Asia and Pacific',
'Australia and New Zealand',
'Caribbean',
'Central America',
'Central Asia and the Caucasus',
'East Asia',
'Eastern Europe ', 
'Europe',
'Middle East (Region)',
'Myanmar',
'North Africa',
'North America',
'Pacific Islands ', 
'South America',
'South Asia',
'Southeast Asia',
'Sub-Saharan Africa (Region) ',
'Western Europe',
'Western Hemisphere (Region)',
'ASEAN-5',
'Advanced economies',
'Emerging and Developing Asia',
'Emerging and Developing Europe',
'Emerging market and developing economies',
'Euro area',
'European Union',
'Latin America and the Caribbean',
'Major advanced economies (G7)',
'Middle East and Central Asia',
'Other advanced economies',
'Sub-Saharan Africa',
'World',
'nan',
'NaN',
'©IMF, 2022'
]


file_model_df.rename(index={'nan':pd.NA},inplace=True)
file_model_df = file_model_df[~file_model_df.index.isin(country_exclusion_list)].dropna()


# file_model_df.to_csv('/Users/stephenontko/Documents/University of Michigan/UMSI/UMSI MADS/UMSI MADS 2023/SIADS 699 Capstone/Data/imf_gdp_pc_target_values.csv',index=False)
# file_model_df.to_csv('imf_gdp_pc_target_values.csv',index=False)

print(file_model_df)

                        1980      1981      1982      1983      1984  \
Country Name                                                           
Afghanistan                0         0         0         0         0   
Albania              728.359   817.734   824.542   815.529   788.332   
Algeria             2268.607  2305.505  2254.328  2316.679  2432.717   
Andorra                    0         0         0         0         0   
Angola               745.119    679.02    661.52   671.804   693.779   
...                      ...       ...       ...       ...       ...   
Vietnam              652.593   318.521   414.347   612.565  1044.409   
West Bank and Gaza         0         0         0         0         0   
Yemen                      0         0         0         0         0   
Zambia               718.795   718.743   672.013   562.441   448.532   
Zimbabwe                   0         0         0         0         0   

                        1985      1986      1987      1988     

Processing Files in Folders for endogenous variables:

In [4]:
# course_file_path = '/Users/stephenontko/Documents/University of Michigan/UMSI/UMSI MADS/UMSI MADS 2023/SIADS 699 Capstone/Data/IMF/'

#files in folders:
files = [
    
        'BOPAGG_02-04-2023 07-59-39-92_timeSeries/BOPAGG_02-04-2023 07-59-39-92_timeSeries.csv'#3
         ,'CDIS_01-15-2023 18-58-45-21_timeSeries/CDIS_01-15-2023 18-58-45-21_timeSeries.csv'
#          ,'CPI_02-07-2023 16-19-35-85_timeSeries/CPI_02-07-2023 16-19-35-85_timeSeries.csv'#6 #too big for github
         ,'ED_02-07-2023 04-41-04-68_timeSeries/ED_02-07-2023 04-41-04-68_timeSeries.csv'
         ,'EQ_02-04-2023 18-05-06-26_timeSeries/EQ_02-04-2023 18-05-06-26_timeSeries.csv'#9
         ,'FAS_02-04-2023 13-20-29-76_timeSeries/FAS_02-04-2023 13-20-29-76_timeSeries.csv'#10
         ,'FDI_07-14-2022 10-45-25-27_timeSeries/FDI_07-14-2022 10-45-25-27_timeSeries.csv'
         ,'FISCALDECENTRALIZATION_11-13-2022 06-45-12-25_timeSeries/FISCALDECENTRALIZATION_11-13-2022 06-45-12-25_timeSeries.csv'
         ,'FM_02-07-2023 04-43-40-20_timeSeries/FM_02-07-2023 04-43-40-20_timeSeries.csv'
         ,'FSI_02-03-2023 08-19-04-78_timeSeries/FSI_02-03-2023 08-19-04-78_timeSeries.csv'#14
         ,'FSIRE_02-04-2023 08-23-40-70_timeSeries/FSIRE_02-04-2023 08-23-40-70_timeSeries.csv'
         ,'GENDER_EQUALITY_01-25-2023 14-59-11-92_timeSeries/GENDER_EQUALITY_01-25-2023 14-59-11-92_timeSeries.csv'#16
#          ,'GFSCOFOG_02-07-2023 04-44-34-74_timeSeries/GFSCOFOG_02-07-2023 04-44-34-74_timeSeries.csv' #too big for github
#          ,'GFSE_02-07-2023 04-44-54-86_timeSeries/GFSE_02-07-2023 04-44-54-86_timeSeries.csv'#18#too big for github
#          ,'GFSFALCS_02-07-2023 04-45-22-02_timeSeries/GFSFALCS_02-07-2023 04-45-22-02_timeSeries.csv'#too big for github
#          ,'GFSIBS_02-06-2023 14-42-18-39_timeSeries/GFSIBS_02-06-2023 14-42-18-39_timeSeries.csv'#too big for github
#          ,'GFSMAB_02-07-2023 04-46-16-64_timeSeries/GFSMAB_02-07-2023 04-46-16-64_timeSeries.csv'#too big for github
#          ,'GFSR_02-07-2023 04-46-55-75_timeSeries/GFSR_02-07-2023 04-46-55-75_timeSeries.csv'#too big for github
#          ,'GFSSSUC_02-07-2023 04-47-28-17_timeSeries/GFSSSUC_02-07-2023 04-47-28-17_timeSeries.csv'#too big for github
        ,'HPDD_04-11-2020 23-37-06-60_timeSeries/HPDD_04-11-2020 23-37-06-60_timeSeries.csv'
#          ,'IFS_02-07-2023 12-51-31-57_timeSeries/IFS_02-07-2023 12-51-31-57_timeSeries.csv'#25#too big for github
#          ,'IRFCL_02-07-2023 08-35-05-78_timeSeries/IRFCL_02-07-2023 08-35-05-78_timeSeries.csv'#26#too big for github
#          ,'PCTOT_01-31-2023 17-02-07-08_timeSeries/PCTOT_01-31-2023 17-02-07-08_timeSeries.csv'#29#too big for github
#          ,'WHDREO_02-06-2023 03-53-04-14_timeSeries/WHDREO_02-06-2023 03-53-04-14_timeSeries.csv' #31#too big for github
#          ,'WoRLD_02-08-2023 01-04-45-48_timeSeries/WoRLD_02-08-2023 01-04-45-48_timeSeries.csv' #32#too big for github
             ] 

#countries or non-countries not in scope
country_exclusion_list = [
'Advanced Economies',
'Advanced Markets',
'Advanced G20',
'Africa',
'Africa (Region)',
'All Countries',
'American Samoa',
'Anguilla',
'Asia and Pacific',
'Australia and New Zealand',
'Belgium-Luxembourg',
'Bermuda',
'Bonaire, St. Eustatius and Saba',
'Bouvet Island',
'British Indian Ocean Territory',
'British Virgin Islands',
'Caribbean',
'CEMAC',
'Central America',
'Central Asia and the Caucasus',
'Central African Economic and Monetary Community',
'CFA franc zone',
'Common Market of Eastern and Southern Africa (COMESA)',
'Cayman Islands',
'Central and South Asia',
'Christmas Island',
'Cocos (Keeling) Islands',
'Cook Islands',
'Curaçao, Kingdom of the Netherlands',
'Curaçao and Sint Maarten',
'Cuba',
'Czechoslovakia',
'East African Community (EAC -5)',
'Economic Community of West African States (ECOWAS)',
'Economies of Persian Gulf',
'East Asia',
'Eastern Caribbean Currency Union',
'Eastern Caribbean Currency Union (ECCU)'
'Eastern Europe ', 
'Emerging G20',
'Emerging Market and Middle-Income Asia ',
'Emerging Market and Middle-Income Economies ',
'Emerging Market and Middle-Income Europe ',
'Emerging Market and Middle-Income Latin America ',
'Emerging Market and Middle-Income Middle East and North Africa and Pakistan',
'Emerging and Developing Countries',
'Emerging and Developing Economies',
'Emerging Markets',
'Europe',
'European Central Bank',
'Faroe Islands',
'French Polynesia',
'French Territories: French Polynesia',
'French Territories: New Caledonia',
'Falkland Islands (Malvinas)',
'French Southern Territories',
'G20',
'G7',
'Gibraltar',
'Greenland',
'Guadeloupe',
'Guernsey',
'Guam',
'Guiana, French',
'Heard Island and McDonald Islands',
'Holy See',
'International Organizations',
'International Organizations and SEFER',
'Isle of Man',
'Jersey',
"Korea, Dem. People's Rep. of",
"Korea, Democratic People's Rep. of",
'Low-Income and Developing Countries',
'Low-Income Developing Asia ',
'Low-Income Developing Latin America',
'Low-Income Developing Others ',
'Low-Income Developing Sub-Saharan Africa',
'Low-Income Oil Producers',
'Liechtenstein',
'Mayotte',
'Monaco',
'Martinique',
'Middle East (Region)',
'Montserrat',
'Netherlands Antilles',
'New Caledonia',
'Niue',
'Norfolk Island',
'North Atlantic and Caribbean',
'North and Central America',
'Northern Mariana Islands',
'Not Specified (including Confidential)',
'North Africa',
'North America',
'Oceania and Polar Regions',
'Other Near and Middle East Economies',
'Pitcairn Islands',
'Pacific Islands ', 
'Reunion',
'Saint Helena',
'Saint Pierre and Miquelon',
'South Georgia and Sandwich Islands',
'Serbia and Montenegro',
'Sint Maarten, Kingdom of the Netherlands',
'South America',
'South Asia',
'Southeast Asia',
'Sub-Saharan Africa (Region) ',
'Tokelau',
'US Pacific Islands',
'United States Virgin Islands',
'Wallis and Futuna Islands',
'Western Sahara',
'Western Europe',
'Western Hemisphere (Region)',
'ASEAN-5',
'Advanced economies',
'Emerging and Developing Asia',
'Emerging and Developing Europe',
'Emerging market and developing economies',
'Emerging and Developing Economies',
'Euro area',
'Euro Area',
'European Union',
'Latin America and the Caribbean',
'Major advanced economies (G7)',
'Middle East and Central Asia',
'Other advanced economies',
'SSA countries in fragile and conflict-affected situations',
'SSA low-income countries',
'SSA low-income countries excluding countries in fragile situations',
'SSA middle-income countries',
'SSA middle-income countries excluding South Africa and Nigeria',
'SSA oil-exporting countries',
'SSA oil-exporting countries excluding Nigeria',
'SSA oil-importing countries',
'SSA oil-importing countries excluding South Africa',
'Southern African Customs Union (SACU)',
'Southern African Development Community (SADC)',
'Sub-Saharan Africa excluding Nigeria and South Africa',
'Sub-saharan Africa',
'Sub-Saharan Africa',
'Swaziland',
'Turks and Caicos Islands',
'Virgin Islands, British',
'West African Economic and Monetary Union (WAEMU)',
'Western Hemisphere',
'World',
'World Minus 25 Significant Financial Centers',
'Yugoslavia',
'nan',
'NaN',
'©IMF, 2022'
]

data_df = pd.DataFrame()

In [5]:
for file in files[:]:
    start_time = time.perf_counter()
    print(file)
#     file_df = pd.read_csv(course_file_path+file)#'/Users/stephenontko/Documents/University of Michigan/UMSI/UMSI MADS/UMSI MADS 2023/SIADS 699 Capstone/Data/imf_gdp_pc_target_values.csv')
    file_df = pd.read_csv(file)
    file_df = file_df[file_df['Attribute']=='Value']
    file_df = file_df[~file_df['Country Name'].isin(country_exclusion_list)]
    
    #edit country names for target value country mapping
    
    file_df=file_df.replace('Afghanistan, Islamic Republic of','Afghanistan')
    file_df=file_df.replace('Afghanistan, Islamic Rep. of','Afghanistan')
    file_df=file_df.replace('Afghanistan, I.R. of','Afghanistan')
    file_df=file_df.replace('Andorra, Principality of','Andorra')
    file_df=file_df.replace('Armenia, Rep. of','Armenia')
    file_df=file_df.replace('Armenia, Republic of','Armenia')
    file_df=file_df.replace('Aruba, Kingdom of the Netherlands','Aruba')
    file_df=file_df.replace('Azerbaijan, Rep. of','Azerbaijan')
    file_df=file_df.replace('Azerbaijan, Republic of','Azerbaijan')
    file_df=file_df.replace('The Bahamas','Bahamas, The')
    file_df=file_df.replace('Bahrain, Kingdom of','Bahrain')
    file_df=file_df.replace('Belarus, Rep. of','Belarus')
    file_df=file_df.replace('Bosnia & Herzegovina','Bosnia and Herzegovina')
    file_df=file_df.replace('Burma ','Burma')
    file_df=file_df.replace('Central African Rep.','Central African Republic')
    file_df=file_df.replace('Equatorial Guinea, Rep. of','Equatorial Guinea')
    file_df=file_df.replace('Eritrea, The State of','Eritrea')
    file_df=file_df.replace('Cape Verde','Cabo Verde')
    file_df=file_df.replace('Comoros, Union of the','Comoros')
    file_df=file_df.replace('Congo, Rep. of','Congo, Republic of ')
    file_df=file_df.replace("Cote d'Ivoire","Côte d'Ivoire")
    file_df=file_df.replace("Democratic Republic of the Congo","Congo, Dem. Rep. of the")
    file_df=file_df.replace("Congo, Democratic Republic of","Congo, Dem. Rep. of the")
    file_df=file_df.replace("Congo, Dem. Rep. of","Congo, Dem. Rep. of the")
    file_df=file_df.replace("Congo, Republic of","Congo, Republic of ")
    file_df=file_df.replace("China","China, People's Republic of")
    file_df=file_df.replace("China,P.R.: Mainland","China, People's Republic of")
    file_df=file_df.replace("China, P.R.: Hong Kong","Hong Kong SAR")
    file_df=file_df.replace("China,P.R.:Hong Kong","Hong Kong SAR")
    file_df=file_df.replace("China, P.R.: Macao","Macao SAR")
    file_df=file_df.replace("China, P.R.: Mainland","China, People's Republic of")
    file_df=file_df.replace('Croatia, Rep. of','Croatia')
    file_df=file_df.replace('Czech Rep.','Czech Republic')
    file_df=file_df.replace('Dominican Rep.','Dominican Republic')
    file_df=file_df.replace('Egypt, Arab Rep. of','Egypt')
    file_df=file_df.replace('Estonia, Rep. of','Estonia')
    file_df=file_df.replace('Ethiopia, The Federal Dem. Rep. of','Ethiopia')
    file_df=file_df.replace('Fiji, Rep. of','Fiji')
    file_df=file_df.replace("Eswatini, Kingdom of","Eswatini")
    file_df=file_df.replace('Iran, Islamic Rep. of','Iran')
    file_df=file_df.replace('Iran, Islamic Republic of','Iran')
    file_df=file_df.replace('Iran, I.R. of','Iran')
    file_df=file_df.replace('Kazakhstan, Rep. of','Kazakhstan')
    file_df=file_df.replace('Korea, Rep. of','Korea, Republic of')
    file_df=file_df.replace('Korea','Korea, Republic of')
    file_df=file_df.replace('Kosovo, Rep. of','Kosovo')
    file_df=file_df.replace('Kosovo, Republic of','Kosovo')
    file_df=file_df.replace('Kyrgyz Rep.','Kyrgyz Republic')
    file_df=file_df.replace("Lao People's Dem. Rep.",'Lao P.D.R.')
    file_df=file_df.replace("Lao People's Dem.Rep",'Lao P.D.R.')
    file_df=file_df.replace('Lesotho, Kingdom of','Lesotho')
    file_df=file_df.replace("Lao People's Democratic Republic","Lao P.D.R.")
    file_df=file_df.replace("Marshall Islands, Republic of","Marshall Islands")
    file_df=file_df.replace("Micronesia, Federated States of","Micronesia, Fed. States of")
    file_df=file_df.replace("Micronesia","Micronesia, Fed. States of")
    file_df=file_df.replace('Madagascar, Rep. of','Madagascar')
    file_df=file_df.replace('Marshall Islands, Rep. of the','Marshall Islands')
    file_df=file_df.replace('Mauritania, Islamic Rep. of','Mauritania')
    file_df=file_df.replace('Moldova, Rep. of','Moldova')
    file_df=file_df.replace('Montenegro, Rep. of','Montenegro')
    file_df=file_df.replace('Mozambique, Rep. of','Mozambique')
    file_df=file_df.replace('Myanmar','Burma')
    file_df=file_df.replace('Nauru, Rep. of','Nauru')
    file_df=file_df.replace('Netherlands, The','Netherlands')
    file_df=file_df.replace('North Macedonia, Republic of','North Macedonia ')
    file_df=file_df.replace('North Macedonia, Republic of ','North Macedonia ')
    file_df=file_df.replace('North Macedonia','North Macedonia ')
    file_df=file_df.replace('Palau, Rep. of','Palau')
    file_df=file_df.replace('Poland, Rep. of','Poland')
    file_df=file_df.replace('Russia','Russian Federation')
    file_df=file_df.replace('San Marino, Rep. of','San Marino')
    file_df=file_df.replace('St. Kitts and Nevis ','Saint Kitts and Nevis')
    file_df=file_df.replace('St. Kitts and Nevis','Saint Kitts and Nevis')
    file_df=file_df.replace('St. Lucia','Saint Lucia')
    file_df=file_df.replace('St. Vincent and the Grenadines','Saint Vincent and the Grenadines')
    file_df=file_df.replace('St. Vincent & Grens.','Saint Vincent and the Grenadines')
    file_df=file_df.replace('St. Lucia','Saint Lucia')
    file_df=file_df.replace("Sao Tome and Principe","São Tomé and Príncipe")
    file_df=file_df.replace("Sao Tome & Principe","São Tomé and Príncipe")
    file_df=file_df.replace("South Sudan","South Sudan, Republic of")
    file_df=file_df.replace('Serbia, Rep. of','Serbia')
    file_df=file_df.replace('Serbia, Republic of','Serbia')
    file_df=file_df.replace('Slovak Rep.','Slovak Republic')
    file_df=file_df.replace('Slovenia, Rep. of','Slovenia')
    file_df=file_df.replace('South Sudan, Rep. of','South Sudan, Republic of')
    file_df=file_df.replace('Syrian Arab Rep.','Syria')
    file_df=file_df.replace('Syrian Arab Republic','Syria')
    file_df=file_df.replace('São Tomé and Príncipe, Dem. Rep. of','São Tomé and Príncipe')
    file_df=file_df.replace("Timor-Leste, Dem. Rep. of","Timor-Leste")
    file_df=file_df.replace('Tajikistan, Rep. of','Tajikistan')
    file_df=file_df.replace('Taiwan Province of China','Taiwan')
    file_df=file_df.replace('Taiwan Prov.of China','Taiwan')
    file_df=file_df.replace('Tanzania, United Rep. of','Tanzania')
    file_df=file_df.replace('Türkiye, Rep of','Türkiye, Republic of')
    file_df=file_df.replace('Turkey','Türkiye, Republic of')
    file_df=file_df.replace('Uzbekistan, Rep. of','Uzbekistan')
    file_df=file_df.replace('Venezuela, Rep. Bolivariana de','Venezuela')
    file_df=file_df.replace('Venezuela, Republica Bolivariana de','Venezuela')
    file_df=file_df.replace('Venezuela, Rep. Bol.','Venezuela')
    file_df=file_df.replace('Yemen Arab Rep.','Yemen')
    file_df=file_df.replace("Yemen, People's Dem. Rep. of",'Yemen')
    file_df=file_df.replace('Yemen, Rep. of','Yemen')
    file_df=file_df.replace('Yemen, Republic of','Yemen')
    
    print(file_df)
    print(file_df.columns)
    indicator_codes = file_df['Indicator Code'].unique()
    print(indicator_codes)
    # print(file_df[file_df['Indicator Code']==indicator_codes[0]])
    # print(file_df[file_df['Indicator Code']==indicator_codes[1]])
    # print(file_df[file_df['Indicator Code']==indicator_codes[2]])
    folder_df = pd.DataFrame(columns=['Country Name','Country Code','Indicator Name'
                                      ,'Indicator Code','Year','Feature Value'])
    for ind_code in indicator_codes[:]:
        print(ind_code)
        var_df = file_df[file_df['Indicator Code']==ind_code]
#         print(var_df.columns)    
        years = []
        for col in var_df.columns:
            try:
                if type(int(col)) is int:
                # print(col)
                    years.append(col)
            except:
                continue
#         print(years)
        if file == 'CDIS_01-15-2023 18-58-45-21_timeSeries/CDIS_01-15-2023 18-58-45-21_timeSeries.csv':
            var_df = var_df[['Country Name','Country Code','Indicator Name','Indicator Code']+years]
            var_df=var_df.set_index(['Country Name', 'Country Code','Indicator Name','Indicator Code']).stack().reset_index()
            var_df.rename(columns={var_df.columns[-2]:'Year',var_df.columns[-1]:'Feature Value'},inplace=True)
            print(var_df)
            var_df['Feature Value'] = var_df['Feature Value'].astype(float)
            var_df=var_df.groupby(['Country Name','Country Code','Indicator Name','Indicator Code','Year'],as_index = False).agg({'Feature Value': np.mean})#.reset_index()#['Feature Value'].sum().reset_index()
            print(var_df)
        elif file =='FISCALDECENTRALIZATION_11-13-2022 06-45-12-25_timeSeries/FISCALDECENTRALIZATION_11-13-2022 06-45-12-25_timeSeries.csv':
            var_df = var_df[['Country Name','Country Code','Indicator Name','Indicator Code','Sector Code']+years]
            var_df['Indicator Code'] = var_df['Indicator Code']+'_'+var_df['Sector Code']
            var_df = var_df[['Country Name','Country Code','Indicator Name','Indicator Code']+years]
            var_df=var_df.set_index(['Country Name', 'Country Code','Indicator Name','Indicator Code']).stack().reset_index()
            var_df.rename(columns={var_df.columns[-2]:'Year',var_df.columns[-1]:'Feature Value'},inplace=True)
            var_df['Feature Value'] = var_df['Feature Value'].astype(float)
            var_df=var_df.groupby(['Country Name','Country Code','Indicator Name','Indicator Code','Year'],as_index = False).agg({'Feature Value': np.mean})#.reset_index()#['Feature Value'].sum().reset_index()
            print(var_df)
        elif file == 'FSIRE_02-04-2023 08-23-40-70_timeSeries/FSIRE_02-04-2023 08-23-40-70_timeSeries.csv':
            var_df = var_df[['Country Name','Country Code','Indicator Name','Indicator Code','Financial Institution Code']+years]
            var_df['Indicator Code'] = var_df['Indicator Code']+'_'+var_df['Financial Institution Code']
            var_df = var_df[['Country Name','Country Code','Indicator Name','Indicator Code']+years]
            var_df=var_df.set_index(['Country Name', 'Country Code','Indicator Name','Indicator Code']).stack().reset_index()
            var_df.rename(columns={var_df.columns[-2]:'Year',var_df.columns[-1]:'Feature Value'},inplace=True)
            var_df['Feature Value'] = var_df['Feature Value'].astype(float)
            var_df=var_df.groupby(['Country Name','Country Code','Indicator Name','Indicator Code','Year'],as_index = False).agg({'Feature Value': np.mean})#.reset_index()#['Feature Value'].sum().reset_index()
            print(var_df)
        else:
            var_df = var_df[['Country Name','Country Code','Indicator Name','Indicator Code']+years]
            var_df=var_df.set_index(['Country Name', 'Country Code','Indicator Name','Indicator Code']).stack().reset_index()
            var_df.rename(columns={var_df.columns[-2]:'Year',var_df.columns[-1]:'Feature Value'},inplace=True)
        print(var_df)
        print(var_df.columns)
        # dt_col_results = dt_col_results.append(iter_df)
        folder_df = folder_df.append(var_df)
        
#     folder_df.to_csv(course_file_path+file.split('/')[0]+'/'+file.split('_')[0]+'_df.csv',index=True)
#     folder_df.to_csv(file.split('/')[0]+'/'+file.split('_')[0]+'_df.csv',index=True)
    print(var_df)
    end_time = time.perf_counter()
    print('Process time: ',f"{end_time-start_time:0.4f} seconds {(end_time-start_time)/60:0.4f} minutes.")

BOPAGG_02-04-2023 07-59-39-92_timeSeries/BOPAGG_02-04-2023 07-59-39-92_timeSeries.csv
                Country Name  Country Code  \
0                  Venezuela           299   
2                 Tajikistan           923   
4                   Thailand           578   
6      Saint Kitts and Nevis           361   
8                     Sweden           144   
...                      ...           ...   
14778             San Marino           135   
14780               Zimbabwe           698   
14782             San Marino           135   
14784             San Marino           135   
14788             San Marino           135   

                                          Indicator Name  Indicator Code  \
0      Financial account, Net lending (+) / net borro...    BFDL_BP6_USD   
2      Current Account, Goods and Services, Services,...     BXS_BP6_USD   
4      Current Account, Goods and Services, Services,...     BXS_BP6_USD   
6              Capital Account, Total, Debit, US Dollars 

/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/2721541501.py:170: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  folder_df = folder_df.append(var_df)
/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/2721541501.py:170: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  folder_df = folder_df.append(var_df)
/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/2721541501.py:170: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  folder_df = folder_df.append(var_df)
/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/2721541501.py:170: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  folder_df = f

BXS_BP6_USD
     Country Name  Country Code  \
0      Tajikistan           923   
1      Tajikistan           923   
2      Tajikistan           923   
3      Tajikistan           923   
4      Tajikistan           923   
...           ...           ...   
3024      Andorra           171   
3025   San Marino           135   
3026   San Marino           135   
3027   San Marino           135   
3028   San Marino           135   

                                         Indicator Name Indicator Code  Year  \
0     Current Account, Goods and Services, Services,...    BXS_BP6_USD  2005   
1     Current Account, Goods and Services, Services,...    BXS_BP6_USD  2006   
2     Current Account, Goods and Services, Services,...    BXS_BP6_USD  2007   
3     Current Account, Goods and Services, Services,...    BXS_BP6_USD  2008   
4     Current Account, Goods and Services, Services,...    BXS_BP6_USD  2009   
...                                                 ...            ...   ...   
3024  C

     Country Name  Country Code  \
0         Senegal           722   
1         Senegal           722   
2         Senegal           722   
3         Senegal           722   
4         Senegal           722   
...           ...           ...   
3010      Andorra           171   
3011   San Marino           135   
3012   San Marino           135   
3013   San Marino           135   
3014   San Marino           135   

                                         Indicator Name Indicator Code  Year  \
0     Current Account, Secondary income, Debit, US D...   BMIS_BP6_USD  2005   
1     Current Account, Secondary income, Debit, US D...   BMIS_BP6_USD  2006   
2     Current Account, Secondary income, Debit, US D...   BMIS_BP6_USD  2007   
3     Current Account, Secondary income, Debit, US D...   BMIS_BP6_USD  2008   
4     Current Account, Secondary income, Debit, US D...   BMIS_BP6_USD  2009   
...                                                 ...            ...   ...   
3010  Current Accou

/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/2721541501.py:170: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  folder_df = folder_df.append(var_df)
/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/2721541501.py:170: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  folder_df = folder_df.append(var_df)
/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/2721541501.py:170: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  folder_df = folder_df.append(var_df)
/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/2721541501.py:170: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  folder_df = f

...

    Country Name  Country Code                   Indicator Name  \
0        Albania           914  Total Assets, Domestic Currency   
1        Albania           914  Total Assets, Domestic Currency   
2        Albania           914  Total Assets, Domestic Currency   
3        Albania           914  Total Assets, Domestic Currency   
4        Algeria           612  Total Assets, Domestic Currency   
..           ...           ...                              ...   
251      Vietnam           582  Total Assets, Domestic Currency   
252      Vietnam           582  Total Assets, Domestic Currency   
253      Vietnam           582  Total Assets, Domestic Currency   
254      Vietnam           582  Total Assets, Domestic Currency   
255      Vietnam           582  Total Assets, Domestic Currency   

          Indicator Code  Year  Feature Value  
0        TA_XDC_FS_ODX_I  2021   1.813312e+12  
1       TA_XDC_FS_ODX_IP  2021   1.813312e+12  
2      TA_XDC_FS_ODX_IPC  2021   1.799784e+12  
3  

/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/2721541501.py:170: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  folder_df = folder_df.append(var_df)
/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/2721541501.py:170: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  folder_df = folder_df.append(var_df)
/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/2721541501.py:170: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  folder_df = folder_df.append(var_df)
/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/2721541501.py:170: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  folder_df = f


    Country Name  Country Code            Indicator Name      Indicator Code  \
0  United States           111  Total Assets, US Dollars     TA_USD_FS_ODX_I   
1  United States           111  Total Assets, US Dollars    TA_USD_FS_ODX_IP   
2  United States           111  Total Assets, US Dollars   TA_USD_FS_ODX_IPC   
3  United States           111  Total Assets, US Dollars  TA_USD_FS_ODX_IPCU   
4  United States           111  Total Assets, US Dollars   TA_USD_FS_ODX_IPS   

   Year  Feature Value  
0  2021   2.421964e+13  
1  2021   2.421964e+13  
2  2021   2.152010e+13  
3  2021   2.059821e+12  
4  2021   6.397185e+11  
Index(['Country Name', 'Country Code', 'Indicator Name', 'Indicator Code',
       'Year', 'Feature Value'],
      dtype='object')
    Country Name  Country Code            Indicator Name      Indicator Code  \
0  United States           111  Total Assets, US Dollars     TA_USD_FS_ODX_I   
1  United States           111  Total Assets, US Dollars    TA_USD_FS_ODX_IP  

                   Country Name  Country Code     Indicator Name  \
0                      Portugal           182  Debt to GDP Ratio   
1                         Qatar           453  Debt to GDP Ratio   
2                       Romania           968  Debt to GDP Ratio   
3            Russian Federation           922  Debt to GDP Ratio   
4                        Rwanda           714  Debt to GDP Ratio   
..                          ...           ...                ...   
186                       Tonga           866  Debt to GDP Ratio   
187  Micronesia, Fed. States of           868  Debt to GDP Ratio   
188                    Mongolia           948  Debt to GDP Ratio   
189                 Afghanistan           512  Debt to GDP Ratio   
190                 Puerto Rico           359  Debt to GDP Ratio   

    Indicator Code Attribute  1800  1801  1802  1803  1804  ...       2007  \
0       GGXWDG_GDP     Value   NaN   NaN   NaN   NaN   NaN  ...  68.439083   
1       GGXWDG_GDP     Valu

/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/2721541501.py:170: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  folder_df = folder_df.append(var_df)
/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/2721541501.py:170: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  folder_df = folder_df.append(var_df)
/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/2721541501.py:170: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  folder_df = folder_df.append(var_df)


Combine All Features From All Files Into Single Dataframe/File

In [6]:

feature_df = pd.DataFrame(columns=['Country Name','Country Code','Indicator Name'
                                      ,'Indicator Code','Year','Feature Value','filename'])
for file_name in files:
    start_time = time.perf_counter()
    print(file_name)
#     print(course_file_path+file_name.split('/')[0]+'/'+file_name.split('_')[0])
#     df_file = pd.read_csv(course_file_path+file_name.split('/')[0]+'/'+file_name.split('_')[0]+'_df.csv')
    df_file = pd.read_csv(file_name.split('/')[0]+'/'+file_name.split('_')[0]+'_df.csv')
    print(df_file)
    print(df_file.columns)
#     df_file = df_file[['Country Name','Country Code','Indicator Name','Indicator Code','Year','Feature Value','filename']]
    df_file = df_file[['Country Name','Country Code','Indicator Name','Indicator Code','Year','Feature Value']]
    print(df_file)
    print(df_file.columns)
    feature_df = feature_df.append(df_file)
    # print(course_file_path+df_file.split('/')[0]+'/metadata_'+df_file.split('/')[1])
    # meta_of_df = pd.read_csv(course_file_path+df_file.split('/')[0]+'/metadata_'+df_file.split('/')[1])
    # meta_of_df = meta_of_df[meta_of_df['Country Name'].isnull() & meta_of_df['Metadata Attribute'].isin(['Dataset','Definition'])].iloc[:,7:8].head()
    # print(meta_of_df)

    # folder_df.to_csv(course_file_path+file.split('/')[0]+'/'+file.split('_')[0]+'_df.csv',index=True)
#     folder_df.to_csv(file.split('/')[0]+'/'+file.split('_')[0]+'_df.csv',index=True)


    end_time = time.perf_counter()
    print('Process time: ',f"{end_time-start_time:0.4f} seconds {(end_time-start_time)/60:0.4f} minutes.")

# feature_df.to_csv('feature_yearly_data_'+str(date.today())+'.csv',index=True)
# feature_df.to_csv('feature_yearly_data_2023-04-01.csv',index=True)


print(feature_df)

BOPAGG_02-04-2023 07-59-39-92_timeSeries/BOPAGG_02-04-2023 07-59-39-92_timeSeries.csv
        Unnamed: 0 Country Name  Country Code  \
0                0    Venezuela           299   
1                1    Venezuela           299   
2                2    Venezuela           299   
3                3    Venezuela           299   
4                4    Venezuela           299   
...            ...          ...           ...   
104487        3018   Uzbekistan           927   
104488        3019   Uzbekistan           927   
104489        3020   Uzbekistan           927   
104490        3021      Andorra           171   
104491        3022      Andorra           171   

                                           Indicator Name Indicator Code  \
0       Financial account, Net lending (+) / net borro...   BFDL_BP6_USD   
1       Financial account, Net lending (+) / net borro...   BFDL_BP6_USD   
2       Financial account, Net lending (+) / net borro...   BFDL_BP6_USD   
3       Financial acc

/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/839523285.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  feature_df = feature_df.append(df_file)


       Unnamed: 0 Country Name  Country Code  \
0               0  Afghanistan           512   
1               1  Afghanistan           512   
2               2  Afghanistan           512   
3               3  Afghanistan           512   
4               4  Afghanistan           512   
...           ...          ...           ...   
68291         676      Uruguay           298   
68292         677      Uruguay           298   
68293         678      Uruguay           298   
68294         679      Uruguay           298   
68295         680    Venezuela           299   

                                          Indicator Name  Indicator Code  \
0      Outward Direct Investment Positions, Derived, ...  IOW_DV_BP6_USD   
1      Outward Direct Investment Positions, Derived, ...  IOW_DV_BP6_USD   
2      Outward Direct Investment Positions, Derived, ...  IOW_DV_BP6_USD   
3      Outward Direct Investment Positions, Derived, ...  IOW_DV_BP6_USD   
4      Outward Direct Investment Positions,

/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/839523285.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  feature_df = feature_df.append(df_file)
/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/839523285.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  feature_df = feature_df.append(df_file)


Process time:  0.1078 seconds 0.0018 minutes.
EQ_02-04-2023 18-05-06-26_timeSeries/EQ_02-04-2023 18-05-06-26_timeSeries.csv
          Unnamed: 0 Country Name  Country Code  \
0                  0      Albania           914   
1                  1      Albania           914   
2                  2      Albania           914   
3                  3      Albania           914   
4                  4      Albania           914   
...              ...          ...           ...   
31292506     3150793     Zimbabwe           698   
31292507     3150794     Zimbabwe           698   
31292508     3150795     Zimbabwe           698   
31292509     3150796     Zimbabwe           698   
31292510     3150797     Zimbabwe           698   

                                        Indicator Name   Indicator Code  Year  \
0         Unit value 95 percent interval - upper bound  uv_UpperBound95  1981   
1         Unit value 95 percent interval - upper bound  uv_UpperBound95  1991   
2         Unit value

...

Process time:  13.1771 seconds 0.2196 minutes.
GENDER_EQUALITY_01-25-2023 14-59-11-92_timeSeries/GENDER_EQUALITY_01-25-2023 14-59-11-92_timeSeries.csv
      Unnamed: 0 Country Name  Country Code            Indicator Name  \
0              0    Mauritius           684   Gender Inequality Index   
1              1    Mauritius           684   Gender Inequality Index   
2              2    Mauritius           684   Gender Inequality Index   
3              3    Mauritius           684   Gender Inequality Index   
4              4    Mauritius           684   Gender Inequality Index   
...          ...          ...           ...                       ...   
5913        2872    Australia           193  Gender Development Index   
5914        2873    Australia           193  Gender Development Index   
5915        2874    Australia           193  Gender Development Index   
5916        2875    Australia           193  Gender Development Index   
5917        2876    Australia           193  G

/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/839523285.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  feature_df = feature_df.append(df_file)


Process time:  12.3892 seconds 0.2065 minutes.
HPDD_04-11-2020 23-37-06-60_timeSeries/HPDD_04-11-2020 23-37-06-60_timeSeries.csv
      Unnamed: 0 Country Name  Country Code     Indicator Name Indicator Code  \
0              0     Portugal           182  Debt to GDP Ratio     GGXWDG_GDP   
1              1     Portugal           182  Debt to GDP Ratio     GGXWDG_GDP   
2              2     Portugal           182  Debt to GDP Ratio     GGXWDG_GDP   
3              3     Portugal           182  Debt to GDP Ratio     GGXWDG_GDP   
4              4     Portugal           182  Debt to GDP Ratio     GGXWDG_GDP   
...          ...          ...           ...                ...            ...   
9517        9517  Puerto Rico           359  Debt to GDP Ratio     GGXWDG_GDP   
9518        9518  Puerto Rico           359  Debt to GDP Ratio     GGXWDG_GDP   
9519        9519  Puerto Rico           359  Debt to GDP Ratio     GGXWDG_GDP   
9520        9520  Puerto Rico           359  Debt to GDP Rati

/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/839523285.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  feature_df = feature_df.append(df_file)


Process time:  128.9141 seconds 2.1486 minutes.
     Country Name Country Code  \
0       Venezuela          299   
1       Venezuela          299   
2       Venezuela          299   
3       Venezuela          299   
4       Venezuela          299   
...           ...          ...   
9517  Puerto Rico          359   
9518  Puerto Rico          359   
9519  Puerto Rico          359   
9520  Puerto Rico          359   
9521  Puerto Rico          359   

                                         Indicator Name Indicator Code  Year  \
0     Financial account, Net lending (+) / net borro...   BFDL_BP6_USD  2005   
1     Financial account, Net lending (+) / net borro...   BFDL_BP6_USD  2006   
2     Financial account, Net lending (+) / net borro...   BFDL_BP6_USD  2007   
3     Financial account, Net lending (+) / net borro...   BFDL_BP6_USD  2008   
4     Financial account, Net lending (+) / net borro...   BFDL_BP6_USD  2009   
...                                                 ...        

Filter training feature data for desired year to train on - year chosen to train will be prior to the target/prediction year

In [7]:

def compile_feature_data(train_year, inputdate):
    print('training year: ',train_year, ' date: ',inputdate)
#     data_df = pd.read_csv(course_file_path+'feature_yearly_data_'+str(inputdate)+'.csv')
    data_df = pd.read_csv('feature_yearly_data_'+str(inputdate)+'.csv')
    data_df=data_df[['Country Name','Indicator Code','Year','Feature Value']]
    train_data_df = data_df[data_df['Year'] <= train_year]
    train_data_df = train_data_df[['Country Name','Indicator Code','Feature Value']]
    train_data_df = pd.pivot_table(train_data_df, values = 'Feature Value'
                                   ,index = ['Country Name']
                                   ,columns = ['Indicator Code']
                                   ,aggfunc=np.mean).fillna(0).astype(float)
    print(train_data_df)
    print(train_data_df.columns)

#     train_data_df.to_csv(course_file_path+'train_feature_data_'+str(train_year)+'_'+str(inputdate)+'.csv',index=True)
#     train_data_df.to_csv('train_feature_data_'+str(train_year)+'_'+str(inputdate)+'.csv',index=True)

    
    test_data_df = data_df[data_df['Year'] <= train_year+1]
    test_data_df = test_data_df[['Country Name','Indicator Code','Feature Value']]
    test_data_df = test_data_df[['Country Name','Indicator Code','Feature Value']]
    test_data_df = pd.pivot_table(test_data_df, values = 'Feature Value'
                                   ,index = ['Country Name']
                                   ,columns = ['Indicator Code']
                                   ,aggfunc=np.mean).fillna(0).astype(float)
    
    exclude_column_list = ['Xgdppc','PPPGDP']#features which too closely represent target values (data leakage)

    for train_column in train_data_df.columns:
        if train_column in exclude_column_list:
            train_data_df = train_data_df.drop(columns =[train_column])
    for test_column in test_data_df.columns:
        if test_column in exclude_column_list:
            test_data_df = test_data_df.drop(columns =[test_column])
#     test_data_df.to_csv(course_file_path+'test_feature_data_'+str(train_year+1)+'_'+str(date.today())+'.csv',index=True)
#     test_data_df.to_csv('test_feature_data_'+str(train_year+1)+'_'+str(inputdate)+'.csv',index=True)
    
train_year = 2020
compile_feature_data(train_year, '2023-04-04')

training year:  2020  date:  2023-04-04
Indicator Code      10RA__XDC  11____EUR     11____USD     11____XDC  \
Country Name                                                           
Afghanistan               0.0        0.0  0.000000e+00  2.491308e+10   
Albania                   0.0        0.0  0.000000e+00  1.092416e+11   
Algeria                   0.0        0.0  0.000000e+00  8.768488e+11   
Andorra                   0.0        0.0  0.000000e+00  0.000000e+00   
Angola                    0.0        0.0  0.000000e+00  8.228547e+11   
...                       ...        ...           ...           ...   
Vietnam                   0.0        0.0  0.000000e+00  4.390028e+14   
West Bank and Gaza        0.0        0.0  3.730317e+08  0.000000e+00   
Yemen                     0.0        0.0  0.000000e+00  6.939473e+11   
Zambia                    0.0        0.0  0.000000e+00  4.693929e+11   
Zimbabwe                  0.0        0.0  0.000000e+00  1.198580e+13   

Indicator Code      12A

In [11]:
#prepare training data

train_model_df = file_model_df.copy()
test_model_df = file_model_df.copy()

def process_data_for_vif(train_year, inputdate):
    print('training year: ',train_year, ' date: ',inputdate)
    
    exclude_column_list = ['Xgdppc','PPPGDP']
    
    exclude_list = ['European Central Bank']

    train_y=train_model_df[[train_year+1]].replace('no data',0).fillna(0)
    test_y=test_model_df[[train_year+2]].replace('no data',0).fillna(0)

#     train_X = pd.read_csv(course_file_path+'train_feature_data_'+str(train_year)+'_'+str(inputdate)+'.csv')
    train_X = pd.read_csv('train_feature_data_'+str(train_year)+'_'+str(inputdate)+'.csv')
    train_X.index = train_X['Country Name']
    train_X = train_X.drop(columns =['Country Name'])
    train_X = train_X[~train_X.index.isin(exclude_list)]
    print(train_X)
    print(train_X.columns)
#     test_X = pd.read_csv(course_file_path+'test_feature_data_'+str(train_year+1)+'_'+str(inputdate)+'.csv')
    test_X = pd.read_csv('test_feature_data_'+str(train_year+1)+'_'+str(inputdate)+'.csv')
    test_X.index = test_X['Country Name']
    test_X = test_X.drop(columns =['Country Name'])
    test_X = test_X[~test_X.index.isin(exclude_list)]
    print(test_X)
    print(test_X.columns)
    code_names = train_X.columns
    
    return train_X, code_names#, train_y, test_X, test_y

train_year = 2020
filedate = '2023-04-04'

# train_X, train_y, test_X, test_y, code_names, filename =  process_data_for_model(train_year, filedate)
train_X, code_names =  process_data_for_vif(train_year, filedate)

training year:  2020  date:  2023-04-04
                    10RA__XDC  11____EUR     11____USD     11____XDC  \
Country Name                                                           
Afghanistan               0.0        0.0  0.000000e+00  2.491308e+10   
Albania                   0.0        0.0  0.000000e+00  1.092416e+11   
Algeria                   0.0        0.0  0.000000e+00  8.768488e+11   
Andorra                   0.0        0.0  0.000000e+00  0.000000e+00   
Angola                    0.0        0.0  0.000000e+00  8.228547e+11   
...                       ...        ...           ...           ...   
Vietnam                   0.0        0.0  0.000000e+00  4.390028e+14   
West Bank and Gaza        0.0        0.0  3.730317e+08  0.000000e+00   
Yemen                     0.0        0.0  0.000000e+00  6.939473e+11   
Zambia                    0.0        0.0  0.000000e+00  4.693929e+11   
Zimbabwe                  0.0        0.0  0.000000e+00  1.198580e+13   

                    12A

Measuring Multi-Collinearity for Endogenous Variables via Variance Inflation Factor (VIF)

In [12]:
def calc_variance_inflation_factor(train_X):
    train_X = train_X.dropna()
    train_X = add_constant(train_X)
    train_X_scaled = StandardScaler().fit(train_X).transform(train_X)
    train_X_scaled = add_constant(train_X_scaled)
    # train_X_scaled = MinMaxScaler().fit(train_X).transform(train_X)
    vif = pd.DataFrame()
    vif['features'] = train_X.columns
    vif['feature_sums'] = [x for x in train_X.sum(axis=0)]
    vif = vif[vif['feature_sums']!=0]
    train_X = train_X[vif['features']]
    vif['VIF'] = [variance_inflation_factor(train_X, i) for i in range(train_X.shape[1])]
    return(vif)

# vif_df = calc_variance_inflation_factor(train_X)
# vif_df = vif_df.sort_values(by=['VIF'], ascending=False).round(4)

vif_df = pd.read_csv('vif_train_model_df_2020_2023-04-04.csv')
print(vif_df)
print(vif_df[vif_df['VIF']<5])
print(vif_df[vif_df['VIF']<5].shape)

# vif_df.to_csv(data_model_file_path+'vif_train_model_df_'+str(train_year)+'_'+str(filedate)+'.csv', index=True)
# vif_df.to_csv('vif_train_model_df_'+str(train_year)+'_'+str(filedate)+'.csv', index=True)



       Unnamed: 0                                        features  \
0            2118                            FS_HH_IDG_FSHDDI_XDC   
1            2260                                  FS_NFC_LDD_XDC   
2            2179                                  FS_NFC_AFT_XDC   
3            2182                                   FS_NFC_AF_XDC   
4             143                                       26G___XDC   
...           ...                                             ...   
12505       11165     GROSA_G14_GDP_PT_W0|S1|G1422_S13_XDC_R_B1GQ   
12506        9720  GEOPR_G14_GDP_PT_W0|S1|G2814_S1311B_XDC_R_B1GQ   
12507       11164   GROSA_G14_GDP_PT_W0|S1|G1422_S1321_XDC_R_B1GQ   
12508        9672  GEOPD_G14_GDP_PT_W0|S1|G2811_S1311B_XDC_R_B1GQ   
12509           0                                           const   

       feature_sums     VIF  
0     -1.340678e+19     inf  
1      2.442466e+17     inf  
2      5.849223e+18     inf  
3      2.090460e+19     inf  
4      5.177188e+20  

In [13]:

iso_country_codes = {
    'Afghanistan':4,
'Albania':8,
'Algeria':12,
'American Samoa':16,
'Andorra':20,
'Angola':24,
'Antigua and Barbuda':28,
'Argentina':32,
    'Armenia':51,
    'Aruba':533,
'Australia':36,
'Austria':40,
    'Azerbaijan':31,
    'Bahamas, The':44,
    'Bahrain':48,
'Bangladesh':50,
    'Barbados':52,
    'Belarus':112,
'Belgium':56,
    'Belize':84,
    'Benin':204,
'Bermuda':60,
'Bhutan':64,
'Bolivia':68,
'Bosnia and Herzegovina':70,
'Botswana':72,
    'Brazil':76,
    'Brunei Darussalam':96,
'Bulgaria':100,
    'Burkina Faso':854,
    'Burma':104,
    'Burundi':108,
    'Cabo Verde':132,
'Cambodia':116,
'Cameroon':120,
    'Canada':124,
    'Central African Republic':140,
    'Chad':148,
    'Chile':152,
    "China, People's Republic of":156,
'Colombia':170,
'Comoros':174,
'Congo, Republic of ':178,
'Congo, Dem. Rep. of the':180,
    'Costa Rica':188,
    "Côte d'Ivoire":384,
'Croatia':191,
'Cuba':192,
'Cyprus':196,
'Czech Republic':203,
    'Denmark':208,
    'Djibouti':262,
'Dominica':212,
'Dominican Republic':214,
'Ecuador':218,
    'Egypt':818,
'El Salvador':222,
'Equatorial Guinea':226,
'Eritrea':232,
'Estonia':233,
    'Eswatini':748,
    'Ethiopia':231,
'Falkland Islands':238,
'Faroe Islands':234,
'Fiji':242,
    'Finland':246,
    'France':250,
'Gabon':266,
'Gambia, The':270,
'Georgia':268,
    'Germany':276,
    'Ghana':288,
    'Greece':300,
'Grenada':308,
'Guadeloupe':312,
'Guam':316,
'Guatemala':320,
'Guernsey':831,
'Guinea':324,
'Guinea-Bissau':624,
'Guyana':328,
    'Haiti':332,
    'Honduras':340,
    'Hong Kong SAR':344,
    'Hungary':348,
    'Iceland':352,
    'India':356,
'Indonesia':360,
'Iran':364,
'Iraq':368,
'Ireland':372,
'Israel':376,
'Italy':380,
'Jamaica':388,
'Japan':392,
'Jordan':400,
'Kazakhstan':398,
'Kenya':404,
'Kiribati':296,
"Korea (Democratic People's Republic of)":408,
"Korea, Republic of":410,
    'Kosovo':None,
'Kuwait':414,
'Kyrgyz Republic':417,
"Lao P.D.R.":418,
'Latvia':428,
'Lebanon':422,
'Lesotho':426,
'Liberia':430,
'Libya':434,
'Liechtenstein':438,
'Lithuania':440,
'Luxembourg':442,
'Macao SAR':446,
'Madagascar':450,
'Malawi':454,
'Malaysia':458,
'Maldives':462,
'Mali':466,
'Malta':470,
'Marshall Islands':584,
'Mauritania':478,
'Mauritius':480,
'Mexico':484,
'Micronesia, Fed. States of':583,
'Moldova':498,
'Monaco':492,
'Mongolia':496,
'Montenegro':499,
'Montserrat':500,
'Morocco':504,
'Mozambique':508,
'Namibia':516,
'Nauru':520,
'Nepal':524,
'Netherlands':528,
'New Zealand':554,
'Nicaragua':558,
'Niger':562,
'Nigeria':566,
'Niue':570,
'Norfolk Island':574,
'North Macedonia ':807,
'Northern Mariana Islands':580,
'Norway':578,
    'Oman':512,
'Pakistan':586,
'Palau':585,
'Panama':591,
'Papua New Guinea':598,
'Paraguay':600,
'Peru':604,
'Philippines':608,
'Pitcairn':612,
'Poland':616,
'Portugal':620,
'Puerto Rico':630,
'Qatar':634,
'Romania':642,
'Russian Federation':643,
    'Rwanda':646,
    'Saint Kitts and Nevis':659,
'Saint Lucia':662,
'Saint Martin':663,
'Saint Pierre and Miquelon':666,
'Saint Vincent and the Grenadines':670,
'Samoa':882,
'San Marino':674,
'São Tomé and Príncipe':678,
'Saudi Arabia':682,
'Senegal':686,
'Serbia':688,
'Seychelles':690,
'Sierra Leone':694,
'Singapore':702,
'Slovak Republic':703,
'Slovenia':705,
'Solomon Islands':90,
'Somalia':706,
'South Africa':710,
'South Georgia':239,
    'South Sudan, Republic of':728,
    'Spain':724,
'Sri Lanka':144,
'Sudan':729,
'Suriname':740,
'Sweden':752,
'Switzerland':756,
'Syria':760,
'Taiwan':158,
'Tajikistan':762,
'Tanzania':834,
'Thailand':764,
'Timor-Leste':626,
'Togo':768,
'Tonga':776,
'Trinidad and Tobago':780,
'Tunisia':788,
'Türkiye, Republic of':792,
'Turkmenistan':795,
'Tuvalu':798,
'Uganda':800,
'Ukraine':804,
'United Arab Emirates':784,
'United Kingdom':826,
'United States':840,
'Uruguay':858,
'Uzbekistan':860,
'Vanuatu':548,
'Venezuela':862,
'Vietnam':704,
    'West Bank and Gaza':275,
'Yemen':887,
'Zambia':894,
'Zimbabwe':716
    # ,'nan':None
}


In [14]:
def process_data_for_model(train_year, inputdate):
    print('training year: ',train_year, ' date: ',inputdate)
    train_y=train_model_df[[train_year+1]].replace('no data',0).fillna(0)
    test_y=test_model_df[[train_year+2]].replace('no data',0).fillna(0)

    exclude_list = [ 
        'Eastern Caribbean Currency Union (ECCU)',
        'European Central Bank'
    ]
#     train_X = pd.read_csv(course_file_path+'train_feature_data_'+str(train_year)+'_'+str(inputdate)+'.csv')
    train_X = pd.read_csv('train_feature_data_'+str(train_year)+'_'+str(inputdate)+'.csv')
    train_X.index = train_X['Country Name']
    train_X = train_X.drop(columns =['Country Name'])
    train_X = train_X[~train_X.index.isin(exclude_list)]
#     print(train_X)
#     print(train_X.columns)
#     test_X = pd.read_csv(course_file_path+'test_feature_data_'+str(train_year+1)+'_'+str(inputdate)+'.csv')
    test_X = pd.read_csv('test_feature_data_'+str(train_year+1)+'_'+str(inputdate)+'.csv')
    test_X.index = test_X['Country Name']
    test_X = test_X.drop(columns =['Country Name'])
    test_X = test_X[~test_X.index.isin(exclude_list)]
#     print(test_X)
#     print(test_X.columns)
    code_names = train_X.columns
    
    train_data_to_fit_model = train_y.merge(train_X  , left_on='Country Name', right_on='Country Name', how='inner')#.reset_index()
#     print(train_data_to_fit_model)
#     print(train_data_to_fit_model.columns)

    test_data_to_fit_model = test_y.merge(test_X  , left_on='Country Name', right_on='Country Name', how='inner')#.reset_index()
#     print(test_data_to_fit_model)
#     print(test_data_to_fit_model.columns)
    
    train_df = train_data_to_fit_model.iloc[:,:]
    test_df = test_data_to_fit_model.iloc[:,:]
    
    train_X = train_df.drop(columns =[train_year+1])
    train_y = train_df[[train_year+1]]

    test_X = test_df.drop(columns =[train_year+2])
    test_y = test_df[[train_year+2]]

    feature_list = [x for x in train_X.columns]
    feature_list = [x for x in feature_list if x in test_X.columns]

    train_X = train_X[feature_list]
    test_X = test_X[feature_list]
    
#     print(train_X)
#     print(test_X)
    
    return train_X, train_y, test_X, test_y, code_names

train_year = 2020
filedate = '2023-04-04'

train_X, train_y, test_X, test_y, code_names =  process_data_for_model(train_year, filedate)


training year:  2020  date:  2023-04-04


In [15]:
# metadata_df = pd.read_csv(course_file_path+'/file_metadata_df.csv')


metadata_df = pd.DataFrame(columns = ['file','file_description','column_code','column_name'])

def file_metadata_processing(metafile,metadata_df):
    print(metafile)
    meta_file_df = pd.read_csv(metafile.split('/')[0]+'/metadata_'+metafile.split('/')[1])
    meta_file_description = meta_file_df[meta_file_df['Country Name'].isnull() & meta_file_df['Metadata Attribute'].isin(['Dataset','Definition'])].iloc[:,7:8].head()
    print(meta_file_description)
#     print(meta_file_df)
#     print(meta_file_df.columns)
    try:
#         print(metafile)
#         print(meta_file_df)
#         print(meta_file_df.columns)
        meta_file_df = meta_file_df[['Indicator Name','Indicator Code','Metadata Attribute','Metadata Value']]
        column_names = meta_file_df['Indicator Name'].unique()
        code_names = meta_file_df['Indicator Code'].unique()
    except:
        print(metafile)
        print(meta_file_df)
        print(meta_file_df.columns)
        if metafile == 'HPDD_04-11-2020 23-37-06-60_timeSeries/HPDD_04-11-2020 23-37-06-60_timeSeries.csv':
            code_names=meta_file_df[meta_file_df['Metadata Attribute']=='Indicator Code']['Metadata Value'].unique()
            column_names=meta_file_df[meta_file_df['Metadata Attribute']=='Indicator Name']['Metadata Value'].unique()
        else:
            meta_file_df = meta_file_df[['Indicator Name','Indicator Source Code','Metadata Attribute','Metadata Value']]
            column_names = meta_file_df['Indicator Name'].unique()
            code_names = meta_file_df['Indicator Source Code'].unique()
#     file_columns[metafile] = [column_names, code_names]
    print(meta_file_df)
    print(meta_file_df.columns)
    print(column_names)
    print(code_names)
    print(len(column_names))
    for colm,codenam in zip(column_names, code_names):
        print(colm,codenam )
        # file_column_names_df.append()
        appendrow = []
        metadata_df = pd.concat([metadata_df,pd.DataFrame([[metafile,meta_file_description,codenam,colm ]]
                                      ,columns = ['file','file_description','column_code','column_name'])])
    return metadata_df

for metafile in files[:]:
    print(metafile)
    metadata_df=file_metadata_processing(metafile,metadata_df)


# print(file_column_names_df)
# metadata_df.to_csv('file_metadata_df.csv', index=True)

BOPAGG_02-04-2023 07-59-39-92_timeSeries/BOPAGG_02-04-2023 07-59-39-92_timeSeries.csv
BOPAGG_02-04-2023 07-59-39-92_timeSeries/BOPAGG_02-04-2023 07-59-39-92_timeSeries.csv
                                      Metadata Value
1                          Balance of Payments (BOP)
2  BOPSY Global Tables aggregate country data by ...
                                         Indicator Name Indicator Code  \
0                                                   NaN            NaN   
1                                                   NaN            NaN   
2                                                   NaN            NaN   
3                                                   NaN            NaN   
4                                                   NaN            NaN   
...                                                 ...            ...   
2943  Supplementary Items, Services balance as a per...   BSGST_BP6_PT   
2944  Supplementary Items, Services balance as a per...   BSGST_BP6_PT   
294

2  The dataset contains nine indices that summari...
               Indicator Name Indicator Code     Metadata Attribute  \
0                         NaN            NaN               Category   
1                         NaN            NaN                Dataset   
2                         NaN            NaN             Definition   
3                         NaN            NaN              Frequency   
4                         NaN            NaN    Geographic Coverage   
...                       ...            ...                    ...   
2101  Financial Markets Index       FD_FM_IX         Indicator Name   
2102  Financial Markets Index       FD_FM_IX   Indicator Short Name   
2103  Financial Markets Index       FD_FM_IX  Indicator Source Code   
2104  Financial Markets Index       FD_FM_IX        Indicator Topic   
2105  Financial Markets Index       FD_FM_IX         Indicator Unit   

                                         Metadata Value  
0                                   

Financial Soundness Indicators, Balance Sheets and Income Statements, Households, Gross disposable income, Less taxes including social security contributions, and other current transfers, Euros FS_HH_IDGL_EUR
Financial Soundness Indicators, Balance Sheets and Income Statements, Households, Gross disposable income, Less taxes including social security contributions, and other current transfers, National Currency FS_HH_IDGL_XDC
Financial Soundness Indicators, Balance Sheets and Income Statements, Households, Gross disposable income, Less taxes including social security contributions, and other current transfers, US Dollars FS_HH_IDGL_USD
Financial Soundness Indicators, Balance Sheets and Income Statements, Households, Gross disposable income, National Currency FS_HH_IDG_XDC
Financial Soundness Indicators, Balance Sheets and Income Statements, Households, Gross disposable income, Other, Euros FS_HH_IDGO_EUR
Financial Soundness Indicators, Balance Sheets and Income Statements, Households, 

Monetary and Financial Accounts, Financial Soundness Indicators, Balance Sheets and Income Statements, Deposit takers, Memorandum Series, Supervisory-based series, Common Equity Tier 1 capital, Common Equity Tier 1 capital to risk-weighted assets, Euros FS_ODX_CET1_FSCET_EUR
Monetary and Financial Accounts, Financial Soundness Indicators, Balance Sheets and Income Statements, Deposit takers, Memorandum Series, Supervisory-based series, Common Equity Tier 1 capital, Common Equity Tier 1 capital to risk-weighted assets, US Dollars FS_ODX_CET1_FSCET_USD
Monetary and Financial Accounts, Financial Soundness Indicators, Balance Sheets and Income Statements, Deposit takers, Memorandum Series, Supervisory-based series, Common Equity Tier 1 capital, Domestic Currency FS_ODX_CET1_XDC
Monetary and Financial Accounts, Financial Soundness Indicators, Balance Sheets and Income Statements, Deposit takers, Memorandum Series, Supervisory-based series, Common Equity Tier 1 capital, Euros FS_ODX_CET1_EUR

Monetary and Financial Accounts, Financial Soundness Indicators, Balance Sheets and Income Statements, Other financial corporations, Insurance Corporations, Income and Expense Statement, Other operating expenses, Other expenses, Domestic Currency FS_OFM_IPF_IC_OEO_XDC
Monetary and Financial Accounts, Financial Soundness Indicators, Balance Sheets and Income Statements, Other financial corporations, Insurance Corporations, Income and Expense Statement, Other operating expenses, Other expenses, Euros FS_OFM_IPF_IC_OEO_EUR
Monetary and Financial Accounts, Financial Soundness Indicators, Balance Sheets and Income Statements, Other financial corporations, Insurance Corporations, Income and Expense Statement, Other operating expenses, Other expenses, US Dollars FS_OFM_IPF_IC_OEO_USD
Monetary and Financial Accounts, Financial Soundness Indicators, Balance Sheets and Income Statements, Other financial corporations, Insurance Corporations, Income and Expense Statement, Other operating expenses,

Monetary and Financial Accounts, Financial Soundness Indicators, Balance Sheets and Income Statements, Other financial corporations, Non-Life Insurance Corporations, Balance Sheet, Liabilities, Insurance, pensions, and standardized guarantee schemes, Pension fund reserves, Euros FS_OFM_IPF_NLIC_LIPF_EUR
Monetary and Financial Accounts, Financial Soundness Indicators, Balance Sheets and Income Statements, Other financial corporations, Non-Life Insurance Corporations, Balance Sheet, Liabilities, Insurance, pensions, and standardized guarantee schemes, Pension fund reserves, US Dollars FS_OFM_IPF_NLIC_LIPF_USD
Monetary and Financial Accounts, Financial Soundness Indicators, Balance Sheets and Income Statements, Other financial corporations, Non-Life Insurance Corporations, Balance Sheet, Liabilities, Insurance, pensions, and standardized guarantee schemes, Prepayment of insurance premiums and insurance payable, Domestic Currency FS_OFM_IPF_NLIC_LIPI_XDC
Monetary and Financial Accounts, Fi

  Financial Institution Code
1                        NaN
2                        NaN
     Indicator Name Indicator Code                        Metadata Attribute  \
0               NaN            NaN                                  Category   
1               NaN            NaN                                   Dataset   
2               NaN            NaN                                Definition   
3               NaN            NaN                                 Frequency   
4               NaN            NaN                       Geographic Coverage   
...             ...            ...                                       ...   
3212            NaN            NaN                Financial Institution Name   
3213            NaN            NaN  Financial Institution Original EcOS Code   
3214            NaN            NaN           Financial Institution SDMX Code   
3215            NaN            NaN           Financial Institution SDMX Name   
3216            NaN            Na

Creating Decision Tree Model Function
Model within a model is also being processed - the first decition tree is used to evaluated the significant 
features of the data, which is then fed into the second decision tree for more honed model predition

In [16]:
dt_col_results = pd.DataFrame(columns = ['filename', 'train_year', 'first_model_score', 'second_model_score', 'max_features','max_depth','ccp_alpha','percent_threshold','column','column_significance', 'column_descr'])

def dt_w_sig_cols(train_year, date, max_features, max_depth, ccp_alpha, percent_threshold,iteration):

    train_X, train_y, test_X, test_y, code_names =  process_data_for_model(train_year, filedate)


#     feature_list = [x for x in train_X.columns]
#     feature_list = [x for x in feature_list if x in test_X.columns]

#     train_X = train_X[feature_list].dropna()
#     test_X = test_X[feature_list].dropna()

    random_state = 0
    max_features = 'auto'
    max_depth = 20
    
    dt_init_regr = DecisionTreeRegressor(max_features= max_features, max_depth= max_depth, ccp_alpha = ccp_alpha).fit(train_X, train_y)
    dt_regr_predict = dt_init_regr.predict(test_X)
    dt_init_regr_score = dt_init_regr.score(test_X,test_y)
    
    significant_score_indicies =[list(dt_init_regr.feature_importances_).index(x) for x in dt_init_regr.feature_importances_ if x > percent_threshold]
    sig_list = []
    for sig_i, sig_column in enumerate([code_names[x] for x in [list(dt_init_regr.feature_importances_).index(x) for x in dt_init_regr.feature_importances_ if x > percent_threshold]]):
        sig_col_score = round([dt_init_regr.feature_importances_[x] for x in [list(dt_init_regr.feature_importances_).index(x) for x in dt_init_regr.feature_importances_ if x > percent_threshold]][sig_i]*100,6)
        try:
            sig_col_meta_descr = metadata_df[metadata_df['column_code']==sig_column]['column_name'].unique()[0]
        except:
            sig_col_meta_descr = None
        sig_list.append((sig_col_score ,sig_column, sig_col_meta_descr))
    sig_list = sorted(sig_list)
    
    train_X = train_X.iloc[:,significant_score_indicies]
    test_X = test_X.iloc[:,significant_score_indicies]

    print('second data model for significant columns')
    dt_regr2 = DecisionTreeRegressor(max_features= max_features,max_depth= max_depth, ccp_alpha = ccp_alpha).fit(train_X, train_y)
    dt_regr_predict2 = dt_regr2.predict(test_X)    
    dt_regr_score2 = dt_regr2.score(test_X,test_y)
    for sig_i, sig_column in enumerate([code_names[x] for x in [list(dt_init_regr.feature_importances_).index(x) for x in dt_init_regr.feature_importances_ if x > percent_threshold]]):
        sig_col_score = round([dt_init_regr.feature_importances_[x] for x in [list(dt_init_regr.feature_importances_).index(x) for x in dt_init_regr.feature_importances_ if x > percent_threshold]][sig_i]*100,6)
        try:
            sig_col_meta_descr = metadata_df[metadata_df['column_code']==sig_column]['column_name'].unique()[0]
        except:
            sig_col_meta_descr = None
        iter_df = pd.DataFrame([[train_year,dt_regr_score2, dt_init_regr_score, max_features, max_depth, ccp_alpha, percent_threshold, sig_column ,sig_col_score,sig_col_meta_descr, iteration]]
                               ,columns = ['train_year', 'first_model_score', 'second_model_score', 'max_features','max_depth','ccp_alpha','percent_threshold','column','column_significance', 'column_descr','iteration'])
        global dt_col_results
        dt_col_results = dt_col_results.append(iter_df)
    
    # print(mean_squared_error(Y_test, Y_predicted))
    # print(math.sqrt(mean_squared_error(Y_test, Y_predicted)))

    rmse = round(math.sqrt(mean_squared_error(test_y, dt_regr_predict2)),3)
        
    return dt_regr2, train_year, test_y, dt_regr_predict2, dt_regr_score2, max_features, max_depth, ccp_alpha, dt_init_regr_score, rmse

    

Dataframe Processing to input Data into Choropleth World Map

In [17]:
def choropleth_dfs(test_y, train_year, predictions):
    choropleth_df = test_y.copy().astype(float)
    choropleth_df['Country Name'] = choropleth_df.index
    choropleth_df['GDP Per Capita'] = [x for x in predictions]
    choropleth_df['id'] = [iso_country_codes[x] for x in choropleth_df.index]

    choropleth_actual_df = choropleth_df[['Country Name',train_year+2,'id']]
    choropleth_actual_df.rename(columns={train_year+2:'GDP Per Capita'},inplace=True)
    choropleth_actual_df = choropleth_actual_df[['Country Name','GDP Per Capita','id']]

    choropleth_df = choropleth_df[['Country Name','GDP Per Capita','id']]
    return choropleth_df, choropleth_actual_df

Choropleth Process for Mapping GDP Per Capita Results from Model onto the Map

In [18]:
world = alt.topo_feature(data.world_110m.url, feature='countries')

def chart_compilation(choropleth_df, choropleth_actual_df, train_year, model, model_score, rmse):
    gdpactual= alt.Chart(
        world
          , title = ["Actual GDP Per Capita"
                    ,'for Year: ' + str(train_year +2)]).mark_geoshape(stroke='black' #'white'
                                                                ,fillOpacity=1,strokeWidth=.05).transform_lookup(
    lookup='id',
    from_=alt.LookupData(data=choropleth_actual_df, key = 'id', fields=['id','Country Name','GDP Per Capita'])
    ).encode(
    # tooltip='properties.geounit:N',
    color=alt.Color('GDP Per Capita:Q'
                    ,scale= alt.Scale(domain=[
                                                # 0,100000
                                            choropleth_actual_df['GDP Per Capita'].min()
                                              ,choropleth_actual_df['GDP Per Capita'].max()
                                              ]
                                        # ,range=['red','yellow','green']
                                        ,range=['lightgreen','darkblue']
                                      ))
    , tooltip=['Country Name:N', 'GDP Per Capita:Q']

    ).project(
    type='mercator'
    ).properties(
#     width=800,
#     height=800
    width=400,
    height=400
    )
    gdpactual#.show()

    gdpforecast= alt.Chart(
        world
          , title = ["GDP Per Capita Forecasting : "
                    ,'Forecast Year: ' + str(train_year +2) 
                    ,'Model: '+model.__class__.__name__+ ' Score: '+str(round(model_score,4))
                    +' RMSE: '+str(rmse)]
                    ).mark_geoshape(stroke='black' #'white'
                                    ,fillOpacity=1,strokeWidth=.05).transform_lookup(
    lookup='id',
    from_=alt.LookupData(data=choropleth_df, key = 'id', fields=['id','Country Name','GDP Per Capita'])
    ).encode(
    # tooltip='properties.geounit:N',
    color=alt.Color('GDP Per Capita:Q'
                    ,scale= alt.Scale(domain=[
                                           # 0
                                        choropleth_df['GDP Per Capita'].min()
                                              ,choropleth_df['GDP Per Capita'].max()]
                                        # ,range=['red','yellow','green']
                                        ,range=['lightgreen','darkblue']
                                      ))
    , tooltip=['Country Name:N', 'GDP Per Capita:Q']

    ).project(
    type='mercator'
    ).properties(
#     width=800,
#     height=800
    width=400,
    height=400
    )
    gdpforecast#.show()
    return alt.hconcat(gdpactual, gdpforecast)

In [19]:

train_year = 2020
filedate = '2023-04-04'

model, train_year, test_y, predictions, model_score, max_features, max_depth, ccp_alpha, dt_init_regr_score, rmse = dt_w_sig_cols(train_year, filedate, 'auto', 20, .1,.009,1)
choropleth_df, choropleth_actual_df = choropleth_dfs(test_y, train_year, predictions)
chart_compilation(choropleth_df, choropleth_actual_df, train_year, model, model_score, rmse)#.show()


chart_iterations_dict = {}

iter_num = 5
for iter in range(1,iter_num):
    iter_df = dt_col_results[dt_col_results['iteration'] == iter].sort_values(by=['column_significance'], ascending=False).iloc[:10,:]

    print(iter_df)
    iter_df['count'] = iter_df['column']
    iter_df['count'] = [dt_col_results.groupby(['column']).size().loc[x] for x in iter_df['column']]
    print(iter_df.columns)


    chart_iterations_dict[iter] = alt.Chart(iter_df).mark_bar().encode(
    x = alt.X('column_significance:Q',scale = alt.Scale(domain=[dt_col_results['column_significance'].min(),
                                                                dt_col_results['column_significance'].max()])),  
    y="column:O"
    , tooltip='column_descr:O',

    color=alt.Color('count:Q', scale= alt.Scale(range=['lightgreen','darkblue'] ))

    ).properties(height=100, width = 700)

    print(iter_df)
    print(iter_df.columns)


choropleth_df, choropleth_actual_df = choropleth_dfs(test_y, train_year, predictions)

training year:  2020  date:  2023-04-04
second data model for significant columns


/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/1532929725.py:49: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dt_col_results = dt_col_results.append(iter_df)
/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/1532929725.py:49: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dt_col_results = dt_col_results.append(iter_df)
/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/1532929725.py:49: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dt_col_results = dt_col_results.append(iter_df)
/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/1532929725.py:49: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.co

  filename train_year first_model_score second_model_score max_features  \
0      NaN       2020           0.97659            0.95848         auto   
0      NaN       2020           0.97659            0.95848         auto   
0      NaN       2020           0.97659            0.95848         auto   
0      NaN       2020           0.97659            0.95848         auto   
0      NaN       2020           0.97659            0.95848         auto   
0      NaN       2020           0.97659            0.95848         auto   
0      NaN       2020           0.97659            0.95848         auto   
0      NaN       2020           0.97659            0.95848         auto   

  max_depth ccp_alpha percent_threshold  \
0        20       0.1             0.009   
0        20       0.1             0.009   
0        20       0.1             0.009   
0        20       0.1             0.009   
0        20       0.1             0.009   
0        20       0.1             0.009   
0        20       0.1  

/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/100228826.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  choropleth_actual_df.rename(columns={train_year+2:'GDP Per Capita'},inplace=True)


Choropleth Chart comparing actual forecast year GDP Per Capita for countries (on the left) and what the model predicts GDP Per Capita would be for each country for the forecast year (on the right):

In [20]:
chart_compilation(choropleth_df, choropleth_actual_df, train_year, model, model_score,rmse
                 )#.show()


alt.HConcatChart(...)

Top 5 Feature Significance Scores from Decision Tree Model

In [21]:
iter_df=dt_col_results[dt_col_results['iteration'] == 1].sort_values(by=['column_significance'], ascending=False).iloc[:10,:]

# print(iter_df)
iter_df['count'] = iter_df['column']
iter_df['count'] = [dt_col_results.groupby(['column']).size().loc[x] for x in iter_df['column']]
# print(iter_df.columns)


alt.Chart(iter_df).mark_bar().encode(
    x = alt.X('column_significance:Q',scale = alt.Scale(domain=[dt_col_results['column_significance'].min(),
                                                                dt_col_results['column_significance'].max()])),  
    y="column:O"
    , tooltip='column_descr:O',

    color=alt.Color('count:Q', scale= alt.Scale(range=['lightgreen','darkblue'] ))

    ).properties(height=100, width = 700)#.show()



alt.Chart(...)

In [22]:
def choropleth_prcnt_dfs(train_y,test_y, train_year, predictions):

    actual_differences_df = pd.concat([train_y,test_y],axis=1,join='inner').astype(float)
    actual_differences_df['Country Name'] = actual_differences_df.index
    actual_differences_df.index.rename('Country Name', inplace=True)
#     choropleth_prcnt_df['GDP Per Capita'] = [x for x in predictions]
    actual_differences_df['id'] = [iso_country_codes[x] for x in actual_differences_df.index]

    actual_differences_df['predictions'] = [x for x in predictions]

    actual_differences_df['Percent Difference From Actual'] =(actual_differences_df[train_year+2]-actual_differences_df['predictions'])/actual_differences_df[train_year+2]*-100
    actual_differences_df.rename(columns={train_year+2:'GDP Per Capita'},inplace=True)
    actual_differences_df = actual_differences_df[['Country Name','GDP Per Capita','id','Percent Difference From Actual']].fillna(0)
    actual_differences_df = actual_differences_df.replace(0,np.NaN)
    print(actual_differences_df)
#     print([x-test_y.iloc[x,:] for x in train_y.index])
    return actual_differences_df# choropleth_prcnt_df, choropleth_prcnt_actual_df

choropleth_actual_differences_df = choropleth_prcnt_dfs(train_y,test_y, train_year, predictions)



                          Country Name  GDP Per Capita     id  \
Country Name                                                    
Afghanistan                Afghanistan             NaN    4.0   
Albania                        Albania        6369.009    8.0   
Algeria                        Algeria        4151.437   12.0   
Andorra                        Andorra       40722.630   20.0   
Angola                          Angola        3790.704   24.0   
...                                ...             ...    ...   
Vietnam                        Vietnam        4162.938  704.0   
West Bank and Gaza  West Bank and Gaza        3517.363  275.0   
Yemen                            Yemen         873.903  887.0   
Zambia                          Zambia        1348.360  894.0   
Zimbabwe                      Zimbabwe        2420.220  716.0   

                    Percent Difference From Actual  
Country Name                                        
Afghanistan                                    N

Failure Analysis Choropleth Chart:

In [23]:

def chart_diff_compilation(choropleth_actual_differences_df, train_year, model, model_score, rmse):
#     gdpactual= alt.Chart(
#         world
#           , title = ["Actual GDP Per Capita"
#                     ,'for Year: ' + str(train_year +2)]).mark_geoshape(stroke='black' #'white'
#                                                                 ,fillOpacity=1,strokeWidth=.05).transform_lookup(
#     lookup='id',
#     from_=alt.LookupData(data=choropleth_actual_differences_df, key = 'id', fields=['id','Country Name','GDP Per Capita'])
#     ).encode(
#     # tooltip='properties.geounit:N',
#     color=alt.Color('GDP Per Capita:Q'
#                     ,scale= alt.Scale(domain=[
#                                                 # 0,100000
#                                             choropleth_actual_differences_df['GDP Per Capita'].min()
#                                               ,choropleth_actual_differences_df['GDP Per Capita'].max()
#                                               ]
#                                         # ,range=['red','yellow','green']
#                                         ,range=['lightgreen','darkblue']
#                                       ))
#     , tooltip=['Country Name:N', 'GDP Per Capita:Q']

#     ).project(
#     type='mercator'
#     ).properties(
# #     width=800,
# #     height=800
#     width=400,
#     height=400
#     )
#     gdpactual#.show()

    gdpforecast= alt.Chart(
        world
          , title = ["GDP Per Capita Difference From Actual: "
                    ,'Forecast Year: ' + str(train_year +2) 
                    ,'Model: '+model.__class__.__name__+ ' Score: '+str(round(model_score,4))
                    +' RMSE: '+str(rmse)]
                    ).mark_geoshape(stroke='black' #'white'
                                    ,fillOpacity=1,strokeWidth=.05).transform_lookup(
    lookup='id',
    from_=alt.LookupData(data=choropleth_actual_differences_df, key = 'id', fields=['Country Name','id','Percent Difference From Actual'])
    ).encode(
    # tooltip='properties.geounit:N',
    color=alt.Color('Percent Difference From Actual:Q'
                    ,scale= alt.Scale(
#                         domain=[    choropleth_actual_differences_df['Percent Difference From Actual'].min()
#                                     ,choropleth_actual_differences_df['Percent Difference From Actual'].max()
#                                ],
#                                         choropleth_actual_differences_df['Percent Difference From Actual'].min()
#                                               ,choropleth_actual_differences_df['Percent Difference From Actual'].max()]
                                        # ,range=['red','yellow','green']
#                                         ,
                        range=['darkred','darkblue']
                                      ))
    , tooltip=['Country Name:N', 'Percent Difference From Actual:Q']

    ).project(
    type='mercator'
    ).properties(
#     width=800,
#     height=800
    width=400,
    height=400
    )
    gdpforecast#.show()
    return  gdpforecast

choropleth_actual_differences_df = choropleth_prcnt_dfs(train_y,test_y, train_year, predictions)

chart_diff_compilation(choropleth_actual_differences_df, train_year, model, model_score, rmse)



                          Country Name  GDP Per Capita     id  \
Country Name                                                    
Afghanistan                Afghanistan             NaN    4.0   
Albania                        Albania        6369.009    8.0   
Algeria                        Algeria        4151.437   12.0   
Andorra                        Andorra       40722.630   20.0   
Angola                          Angola        3790.704   24.0   
...                                ...             ...    ...   
Vietnam                        Vietnam        4162.938  704.0   
West Bank and Gaza  West Bank and Gaza        3517.363  275.0   
Yemen                            Yemen         873.903  887.0   
Zambia                          Zambia        1348.360  894.0   
Zimbabwe                      Zimbabwe        2420.220  716.0   

                    Percent Difference From Actual  
Country Name                                        
Afghanistan                                    N

alt.Chart(...)

Running Decision Tee Model through KFold 10 process, and then averaging the scores/signigifances

In [24]:

# print(train_X,test_X,train_y,test_y)

kf10 = KFold(n_splits = 10)
kf10.get_n_splits(train_X)


k10_fold_r_results = pd.DataFrame(columns = ['r_score','rmse_score'])
k10_fold_pred_results = pd.DataFrame(index = test_y.index)

for i, (train_index, test_index) in enumerate(kf10.split(train_X)):
    print(f"Fold {i}:")
    max_depth = 20
    # max_depth = 500
    # ccp_alpha = .25 #float when increasing from 0 to 1, tree is pruned more to better generalize
    ccp_alpha = .000000000000001

    # percent_threshold = 0.0009

    dt_rgr = DecisionTreeRegressor(max_features= max_features, max_depth= max_depth, ccp_alpha = ccp_alpha).fit(train_X.iloc[train_index,:], train_y.iloc[train_index,:])
    # dt_regr = DecisionTreeRegressor(max_features= max_features).fit(train_X, train_y)
    dt_init_regr_score = dt_rgr.score(train_X.iloc[test_index,:],train_y.iloc[test_index,:])
    print(dt_init_regr_score)
    # print(test_X)
    dt_regr_predict = dt_rgr.predict(test_X)
#     print(dt_regr_predict)
    rmse = round(math.sqrt(mean_squared_error(test_y, dt_regr_predict)),3)
    print(rmse)

    k10_fold_r_results = pd.concat([k10_fold_r_results,pd.DataFrame([[dt_init_regr_score,rmse]],columns = ['r_score','rmse_score'])],axis=0)
    k10_fold_pred_results = pd.concat([k10_fold_pred_results,pd.DataFrame(np.array(dt_regr_predict).reshape(-1,1),columns = [i],index=test_y.index)],axis=1,join='inner')
    # k10_fold_pred_results = pd.concat([k10_fold_pred_results,pd.DataFrame(np.array(dt_regr_predict).reshape(-1,1),columns = [i],index=test_y.index)],axis=1)

# print(k10_fold_r_results)
print(k10_fold_r_results.mean(axis=0))
print(k10_fold_r_results.std(axis=0))
# print(k10_fold_pred_results)
print(k10_fold_pred_results.mean(axis=1))
print(k10_fold_pred_results.std(axis=1))
print(k10_fold_pred_results.shape)

Fold 0:
0.35200209794195136
5724.07
Fold 1:
0.6327914164870021
4533.132
Fold 2:
0.8915173800278184
3330.91
Fold 3:
0.7425582097492557
4549.798
Fold 4:
0.6503718781998297
5609.132
Fold 5:
0.8678761937133943
4364.487
Fold 6:
0.7382044504346491
4617.587
Fold 7:
0.5074986680760529
5087.74
Fold 8:
0.2234378056062466
7839.873
Fold 9:
0.571475772083455
5454.575
r_score          0.617773
rmse_score    5111.130400
dtype: float64
r_score          0.213252
rmse_score    1192.926391
dtype: float64
Country Name
Afghanistan             583.3610
Albania                6156.2738
Algeria                3795.6852
Andorra               27281.5317
Angola                 2965.1421
                         ...    
Vietnam                3395.2039
West Bank and Gaza     7292.8199
Yemen                   640.8551
Zambia                 1167.4096
Zimbabwe               2001.2241
Length: 194, dtype: float64
Country Name
Afghanistan            1844.749458
Albania                 799.459090
Algeria               

In [25]:
# for alpha_denom in range(1,iter_num):
#     print('alpha: ', alpha_denom, alpha_denom/4)
percent_threshold = 0.009
    # percent_threshold = 0.02
    # alpha = alpha_denom/4
alpha = .9
max_depth = 20
max_features = 'auto' #'log2','auto','sqrt'
    # alpha = .9

train_X, train_y, test_X, test_y, code_names =  process_data_for_model(2020, '2023-04-04')

dt_init_regr = DecisionTreeRegressor(max_features= max_features, max_depth= max_depth, ccp_alpha = ccp_alpha).fit(train_X, train_y)
dt_regr_predict = dt_init_regr.predict(test_X)
dt_regr_score = dt_init_regr.score(test_X,test_y)

rmse = round(math.sqrt(mean_squared_error(test_y, dt_regr_predict)),3)
print(test_y)
print(train_y)
print(dt_regr_predict)
print(dt_regr_score, rmse, test_y.sum(),dt_regr_predict.sum(), test_y.sum()-dt_regr_predict.sum())
print(train_y[60:70])
print(dt_regr_predict[60:70])

# print(train_X)
# print(test_X)


choropleth_actual_differences_df = choropleth_prcnt_dfs(train_y,test_y, train_year, dt_regr_predict)

chart_diff_compilation(choropleth_actual_differences_df, train_year, model, dt_regr_score, rmse)




training year:  2020  date:  2023-04-04
                        2022
Country Name                
Afghanistan                0
Albania             6369.009
Algeria             4151.437
Andorra             40722.63
Angola              3790.704
...                      ...
Vietnam             4162.938
West Bank and Gaza  3517.363
Yemen                873.903
Zambia               1348.36
Zimbabwe             2420.22

[194 rows x 1 columns]
                        2021
Country Name                
Afghanistan                0
Albania               6373.3
Algeria             3659.531
Andorra             41873.06
Angola              2352.128
...                      ...
Vietnam               3717.8
West Bank and Gaza  3450.571
Yemen                644.153
Zambia              1095.465
Zimbabwe            2121.568

[194 rows x 1 columns]
[  2121.568   6373.3     3659.531    611.174   2352.128  14809.483
  10616.947   4701.479  28682.797  63464.106  53332.268   5397.928
  28792.071  26135.777  

/var/folders/7l/v039n9y14dl1p58v4l2n14_r0000gn/T/ipykernel_47243/971455253.py:21: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  print(dt_regr_score, rmse, test_y.sum(),dt_regr_predict.sum(), test_y.sum()-dt_regr_predict.sum())


alt.Chart(...)

In [26]:
# choropleth_actual_differences_df = choropleth_actual_differences_df[choropleth_actual_differences_df['Percent Difference From Actual']!='-inf']
# choropleth_actual_differences_df = choropleth_actual_differences_df.replace('-inf',np.NaN)
choropleth_actual_differences_df['prediction_difference_percent_abs'] = abs(choropleth_actual_differences_df['Percent Difference From Actual'])
choropleth_actual_differences_df=choropleth_actual_differences_df.sort_values(by=['prediction_difference_percent_abs'],ascending=False)
choropleth_actual_differences_df = choropleth_actual_differences_df#.iloc[:30,:]
print(choropleth_actual_differences_df)
print(choropleth_actual_differences_df.columns)
forecast_failure_chart = alt.Chart(choropleth_actual_differences_df.iloc[:30, :]
#                                    , title = ["Countries with the Greatest Forecast Discrepancies:"
#                     ,'Forecast Year: ' + str(train_year +2) 
#                     ,'Model: '+model.__class__.__name__+ ' Score: '+str(round(model_score,4))
#                     +' RMSE: '+str(round(rmse,4))]
                    ).mark_geoshape(stroke='black' #'white'
                                    ,fillOpacity=1,strokeWidth=.05
                                   ).mark_bar().encode(
    x = alt.X('Percent Difference From Actual:Q',
#               scale = alt.Scale(domain=[choropleth_actual_differences_df['Percent Difference From Actual'][:30].min(),
#                         choropleth_actual_differences_df['Percent Difference From Actual'][:30].max()])
             ),  
    y=alt.Y("Country Name:O"
            , sort=alt.SortField("prediction_difference_percent_abs", order="descending"))
#            )
    , tooltip='GDP Per Capita:Q',
    color=alt.Color('GDP Per Capita:Q', scale= alt.Scale(range=['darkred','darkblue'] ))
    ).properties(height=900, width = 900)

forecast_failure_chart#.show()

                  Country Name  GDP Per Capita     id  \
Country Name                                            
Afghanistan        Afghanistan             NaN    4.0   
Ukraine                Ukraine             NaN  804.0   
Andorra                Andorra       40722.630   20.0   
Guyana                  Guyana       18744.631  328.0   
Angola                  Angola        3790.704   24.0   
...                        ...             ...    ...   
Botswana              Botswana        7347.738   72.0   
Albania                Albania        6369.009    8.0   
United Kingdom  United Kingdom       47317.565  826.0   
Lebanon                Lebanon             NaN  422.0   
Syria                    Syria             NaN  760.0   

                Percent Difference From Actual  \
Country Name                                     
Afghanistan                                inf   
Ukraine                                    inf   
Andorra                             -98.499178   
Guyana  

alt.Chart(...)